# Starting by building the game and the user interface

In [1]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from keras.models import Sequential
from keras.layers.core import Dense, Dropout, Activation
from keras.optimizers import RMSprop

Using TensorFlow backend.


In [39]:
def showBoard(board):
    '''Shows the board'''
    for val in board:
        print(val)

def checkFree(x,board):
    '''Takes an x,y postion and checks if that point on the board is free'''
    b = board.reshape(1,9)
    if b[0][x] ==0:
        return True
    else:
        return False
def checkWin(toggle, board):
    '''checks wins for each player for diagonals, rows, columns'''
    if toggle:
        high = 6
    else:
        high = 15
    if board.diagonal().sum() == high:
        return True
    if np.flip(board,1).diagonal().sum() == high:
        return True
    for val in range(0,3):
        if board[val,:].sum()==high:
            return True
    for val in range(0,3):
        if board[:,val].sum()==high:
            return True
    return False

def getAvailablePositions(board):
    pos = []
    for i in range(9):
        if checkFree(i,board):
            pos.append(i)
    return pos

def placePiece(x,y,nought_or_cross,board):
    '''Takes a x, y position and a X or O with X=1, and O=2'''
    new_board = np.zeros((3,3))
    for i in range(3):
        for j in range(3):
            new_board [i][j] = board[i][j]
    
    new_board[x,y] = nought_or_cross
    return new_board

def getReward(result,num_moves):
    '''Reward a game won or lost'''
    if result == 'lost':
        return -10+(-num_moves)
    elif result== 'win':
        return 10+(-num_moves)
    else:
        return 0+(-num_moves)
    
def getMove(action):
    '''Gets the move based on the chosen action number'''
    moves = [[0,0],[0,1],[0,2],[1,0],[1,1],[1,2],[2,0],[2,1],[2,2]]
    return moves[action]

def index_map(index, positions):
    return positions[index]

In [3]:
model = Sequential()
model.add(Dense(164, kernel_initializer='lecun_uniform', input_shape=(9,)))
model.add(Activation('relu'))
#model.add(Dropout(0.2)) I'm not using dropout, but maybe you wanna give it a try?

model.add(Dense(150, kernel_initializer='lecun_uniform'))
model.add(Activation('relu'))
#model.add(Dropout(0.2))

model.add(Dense(9, kernel_initializer='lecun_uniform'))
model.add(Activation('linear')) #linear output so we can have range of real-valued outputs

rms = RMSprop()
model.compile(loss='mse', optimizer=rms)

In [61]:
import random
#run function

epsilon = 1
gamma = 0.9


for epoch in range(1,100):
    
    toggle = False
    board = np.zeros((3,3))
    count = 0
    moves = []
    result = 'play'
    
    while result != 'lose' and result != 'win' and result !='draw':
        toggle = not toggle
        qval = model.predict(board.reshape(1,9), batch_size=1)
        if epsilon > random.random():
            action = np.random.choice(getAvailablePositions(board))
        else:
            print(getAvailablePositions(board))
            action = getAvailablePositions(board)[np.argmax(qval[0][getAvailablePositions(board)])]
        move = getMove(action)
        x = move[0]
        y = move[1]
        if toggle == True:
            n_or_c = 5
        else:
            n_or_c = 2
        
        new_board = placePiece(int(x),int(y),n_or_c, board)
        
        if checkWin(toggle, new_board):
             result = 'lose'
        elif checkWin(not toggle, new_board):
            result = 'win'
        elif not getAvailablePositions(new_board):
            result = 'draw'
        
        reward = getReward(result, count)
        
        newQ = model.predict(new_board.reshape(1,9), batch_size=1)
        maxQ = np.max(newQ)
        y = np.zeros((1,9))
        y[:] = qval[:]
        if result != 'lose' or result != 'win' or result !='draw': #non-terminal state
            update = (reward + (gamma * maxQ))
        else: #terminal state
            update = reward
        y[0][action] = update #target output
        print("Game #: %s" % (epoch,))
        model.fit(board.reshape(1,9), y, batch_size=1, epochs=1, verbose=1)
        board = new_board
        #showBoard(board)
        count = count + 1
        if epsilon > 0.1:
            epsilon -= (1/1000)


Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 60.1263
Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.6843
Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 26.7047
Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 61.7450
Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 17.8195
Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 15.0074
Game #: 1
Epoch 1/1
1/1 [==============================] - 0s - loss: 10.2427
Game #: 2
Epoch 1/1
1/1 [==============================] - 0s - loss: 71.4728
Game #: 2
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.5854
Game #: 2
Epoch 1/1
1/1 [==============================] - 0s - loss: 6.0120
Game #: 2
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.7028
Game #: 2
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.4794
Game #: 2
Epoch 1/1
1/1 [==============================] - 0s - loss:

Epoch 1/1
1/1 [==============================] - 0s - loss: 1.4745
Game #: 15
Epoch 1/1
1/1 [==============================] - 0s - loss: 53.7856
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 12.4324
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 13.2486
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.1661
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0150
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.6358
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.5439
Game #: 16
Epoch 1/1
1/1 [==============================] - 0s - loss: 32.9157
Game #: 17
Epoch 1/1
1/1 [==============================] - 0s - loss: 32.2248
[0, 1, 2, 3, 4, 5, 7, 8]
Game #: 17
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.7291
Game #: 17
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.1406
Game #: 17
Epoch 1/1
1/1 [===================

1/1 [==============================] - 0s - loss: 4.3882
[0, 1, 2, 5, 8]
Game #: 28
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1792
Game #: 28
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.8288
[1, 2, 5]
Game #: 28
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.6491
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.9586e-04
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 4.2579
[0, 1, 2, 3, 4, 5, 8]
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 3.0479
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.1823
[0, 2, 3, 5, 8]
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0167
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0932
Game #: 29
Epoch 1/1
1/1 [==============================] - 0s - loss: 3.8734
Game #: 30
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.2764
Game #: 30
Epoch 

Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1506
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1072
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.5635
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1020
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.2127
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0169
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.4313
[5]
Game #: 42
Epoch 1/1
1/1 [==============================] - 0s - loss: 9.2540
Game #: 43
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0144
Game #: 43
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.6165
[0, 1, 2, 3, 6, 7, 8]
Game #: 43
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0526
[0, 1, 3, 6, 7, 8]
Game #: 43
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0561
Game #: 43
Epoch 1/1
1/1 [====

1/1 [==============================] - 0s - loss: 2.8413
[0, 1, 2, 4, 5, 6, 7, 8]
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0055
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0279
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1450
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0045
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.9668
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 3.2047
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.9835
[5]
Game #: 55
Epoch 1/1
1/1 [==============================] - 0s - loss: 5.3380
[0, 1, 2, 3, 4, 5, 6, 7, 8]
Game #: 56
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.2607
Game #: 56
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.6950
Game #: 56
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1999
Game #: 56
Epoch 1/1
1/1 [==

1/1 [==============================] - 0s - loss: 0.0542
Game #: 67
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0353
[3, 6, 8]
Game #: 67
Epoch 1/1
1/1 [==============================] - 0s - loss: 3.4557
[0, 1, 2, 3, 4, 5, 6, 7, 8]
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.2994
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.5937
[0, 2, 3, 5, 6, 7, 8]
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1121
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0139
[0, 2, 3, 5, 6]
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 2.7300e-05
[2, 3, 5, 6]
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 8.7387e-04
[2, 3, 5]
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.4215
Game #: 68
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.4394
[5]
Game #: 68
Epoch 1/1
1/1 [==========================

1/1 [==============================] - 0s - loss: 0.8560
Game #: 80
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1532
[0, 1, 2, 3, 8]
Game #: 80
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.3775
Game #: 80
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.1122
Game #: 80
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.5893
[3, 8]
Game #: 80
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.8542
[0, 1, 2, 3, 4, 5, 6, 7, 8]
Game #: 81
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0953
Game #: 81
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1091
Game #: 81
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0254
[0, 2, 5, 6, 7, 8]
Game #: 81
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.1595
Game #: 81
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.7197
[0, 2, 5, 6]
Game #: 81
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.1473
Ga

1/1 [==============================] - 0s - loss: 1.1303
[0, 1, 2, 5, 6, 7, 8]
Game #: 92
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0196
Game #: 92
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.6102
[0, 1, 5, 6, 8]
Game #: 92
Epoch 1/1
1/1 [==============================] - 0s - loss: 8.9060
[0, 1, 2, 3, 4, 5, 6, 7, 8]
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0130
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.3270
[0, 1, 2, 3, 6, 7, 8]
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0145
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.2047
[0, 2, 3, 6, 8]
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.4906
[2, 3, 6, 8]
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 1.5363
Game #: 93
Epoch 1/1
1/1 [==============================] - 0s - loss: 0.0608
Game #: 93
Epoch 1/1
1/1 [====================

In [54]:
toggle = False
board = np.zeros((3,3))
result = 'play'

while result != 'lose' and result != 'win' and result !='draw':
    toggle = not toggle
    qval = model.predict(board.reshape(1,9), batch_size=1)
    print(getAvailablePositions(board))
    action = getAvailablePositions(board)[(np.argmax(qval[0][getAvailablePositions(board)]))]
    print(action)
    move = getMove(action)
    x = move[0]
    y = move[1]
    if toggle == True:
        n_or_c = 5
    else:
        n_or_c = 2

    new_board = placePiece(int(x),int(y),n_or_c, board)

    if checkWin(toggle, new_board):
         result = 'lose'
    elif checkWin(not toggle, new_board):
        result = 'win'
    elif not getAvailablePositions(new_board):
        result = 'draw'

    board = new_board
    showBoard(board)


[0, 1, 2, 3, 4, 5, 6, 7, 8]
2
[ 0.  0.  5.]
[ 0.  0.  0.]
[ 0.  0.  0.]
[0, 1, 3, 4, 5, 6, 7, 8]
6
[ 0.  0.  5.]
[ 0.  0.  0.]
[ 2.  0.  0.]
[0, 1, 3, 4, 5, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 

[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  

[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  

[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  

[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 

...

[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 

[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 

[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  

[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  5.]
[ 2.  0.  0.]
[0, 1, 3, 4, 7, 8]
5
[ 0.  0.  5.]
[ 0.  0.  2.]
[ 2.  

KeyboardInterrupt: 